In [1]:
import numpy as np
import matplotlib.pyplot as plt
%config InlineBackend.figure_format = 'retina'
import random
%matplotlib qt

In [2]:
#Randomly placing particles from solar wind
x = 800
y = 700
X = x
Y = y
initial = np.zeros((y,x))

In [3]:
def display(A):
    maxY = A.shape[0]
    maxX = A.shape[1]
    B = np.zeros((maxY, maxX))
    for ix in range(0,maxX):
        for iy in range(0,maxY):
            B[maxY-iy-1,ix] = A[iy,ix]

    #Display the graphics outside of the notebook. 
    #On a PC, use '%matplotlib qt' instead.
    
    plt.rcParams['figure.figsize'] = [12, 12/maxX*maxY]
    plt.imshow(B); 
    plt.axis('off'); 
    plt.show()
    plt.draw()
    plt.pause(0.1)

In [4]:
# Distance from Mars
rm = int(Y/2.25)
m = 10
Mars = np.copy(initial)
m1 = np.zeros(x,int)
m2 = np.zeros(x,int)
for i in range(0,y-1):
    if i < (y/2) and i >= (y/2) - rm:
        m1[i] = x - np.sqrt(rm**2 - ((y/2)-i)**2)
        Mars[i,m1[i]:x] = m
    if i >= (y/2) and i < (y/2) + rm + 1:
        m2[i] = x - np.sqrt(rm**2 - (i-(y/2))**2)
        Mars[i,m2[i]:x] = m
    if i < (y/2) - rm:
        m1[i] = x
    if i > (y/2) + rm:
        m2[i] = x   
#display(Mars)  

In [5]:
#Corona
rc = int(Y/1.25)
c = 2
corona = np.copy(Mars)
c1 = np.zeros(x,int)
c2 = np.zeros(x,int)
for i in range(0,y-1):
    if i < (y/2) and i >= (y/2) - rc:
        c1[i] = x - np.sqrt(rc**2 - ((y/2)-i)**2)
        corona[i,c1[i]:m1[i]] = c
    if i >= (y/2) and i < (y/2) + rc + 1:
        c2[i] = x - np.sqrt(rc**2 - (i-(y/2))**2)
        corona[i,c2[i]:m2[i]] = c
    if i < (y/2) - rc:
        c1[i] = x
    if i > (y/2) + rc:
        c2[i] = x  
        
#display(corona) 

In [6]:
#Distance from bowshock
rb = int(Y/1.6)
b = 5
bowshock = np.copy(corona)
b1 = np.zeros(x,int)
b2 = np.zeros(x,int)
for i in range(0,y-1):
    if i < (y/2) and i >= (y/2) - rb:
        b1[i] = x - np.sqrt(rb**2 - ((y/2)-i)**2)
        bowshock[i,b1[i]-1:b1[i]+1] = b
    if i >= (y/2) and i < (y/2) + rb + 1:
        b2[i] = x - np.sqrt(rb**2 - (i-(y/2))**2)
        bowshock[i,b2[i]-1:b2[i]+1] = b
    if i < (y/2) - rb:
        b1[i] = x
    if i > (y/2) + rb:
        b2[i] = x   

#display(bowshock)

In [7]:
p = 15
h = -5
particles = np.copy(bowshock)
particles[0,0] = p
particles[Y-1,X-1] = h
display(particles)

In [12]:
lag = 2
sz = 2
scatter = 10
deposition = np.copy(particles)
travel = np.copy(deposition)
from matplotlib.animation import FFMpegWriter
metadata = dict(title = 'My first animation.mp4', artist = 'Matplotlib')
writer = FFMpegWriter(fps = 15, metadata = metadata)
fig = plt.figure()
nt = 200
with writer.saving(fig, 'solar_wind_5_EPS109_Final.mp4', nt):
    for rep in range(0,5):
        nparticles = int(Y/4)
        ran = np.random.randint(0,Y,nparticles)
        even = []
        for i in ran:
            if (i % 2) == 0:
                even.append(i)
        neven =  int(len(even)/2)
        ran_e = np.random.randint(0,len(even)-1,neven)
        exchg = []
        for k in ran_e:
            exchg.append(even[k])

        d1 = np.zeros(Y,int)
        d2 = np.zeros(Y,int)  
        for j in range(0,X,lag):
            for i in even:
                sp = p #specie = 10 when proton and 1 when hydrogen
                for s in exchg:
                    if i == s:
                        sp = h

                #ran start position 
                if j == 0:
                    #travel[i,j] = p
                    travel[i-sz:i+sz,j-sz:j+sz] = p
         
                    
                #start to corona
                if j <= c1[i]:
                    #travel[i,j] = p
                    travel[i-sz:i+sz,j-sz:j+sz] = p
                    
                if j <= c2[i]:
                    #travel[i,j] = p
                    travel[i-sz:i+sz,j-sz:j+sz] = p
                    
                if sp == h:
                    #traveling trhough corona
                    if j > c1[i] and j < m1[i]-sz:
                        x = np.copy(j)
                        y = np.copy(i)
                        R = np.random.random(); 
                        if R <= 0.40:
                            #left
                            x = x-scatter
                        if R >0.40 and R <=0.70:
                            #up
                            y = y+scatter
                        if R>0.70 and R<=1:
                            #down
                            y = y-scatter
                        
                        r =  np.random.random();
                        echg = sp
                        if r < 0.15:
                            if j > b2[y]: 
                                echg = p
                            if j < b2[y]:
                                sp = p
                    
                        if x < m1[y]-sz-lag:
                            travel[y-sz:y+sz,x-sz:x+sz] = echg
                        
                        if x >= m1[y]-sz-lag and x < m1[y]+lag:
                            if y < Y/2 and y > Y/2 - rm:
                                if deposition[y,x+sz] == c:
                                    deposition[y-sz:y+sz,x-sz:x+sz] = echg
                                elif deposition[y-sz-1,x+sz] == c:
                                    deposition[y-sz-1:y+sz+1,x-sz:x+sz] == echg
                                elif deposition[y+sz+1,x+sz] == c:
                                    deposition[y-sz+1:y+sz-1,x-sz:x+sz] == echg
                                elif deposition[y,x-sz-1] == c:
                                    deposition[y-sz:y+sz,x-sz-1:x+sz-1] == echg
                                travel[y-sz:y+sz,m1[y]-sz:m1[y]+sz] = echg
                            

                    if j > c2[i] and j < m2[i]-sz: 
                        x = np.copy(j)
                        y = np.copy(i)
                        R = np.random.random(); 
                        if R <= 0.40:
                            #left
                            x = x-scatter
                        if R >0.40 and R <=0.70:
                            #up
                            y = y+scatter
                        if R>0.70 and R<=1:
                            #down
                            y = y-scatter
                        
                        r =  np.random.random();
                        echg = sp
                        if r < 0.15:
                            if j > b2[y]: 
                                echg = p
                            if j < b2[y]:
                                sp = p
                            
                        if x < m2[y]-sz-lag:
                            travel[y-sz:y+sz,x-sz:x+sz] = echg
                        
                        if x >= m2[y]-sz-lag and x < m2[y]+lag:
                            if y >= Y/2 and y < Y/2 + rm:
                                if deposition[y,x+sz] == c:
                                    deposition[y-sz:y+sz,x-sz:x+sz] = echg
                                elif deposition[y-sz-1,x+sz] == c:
                                    deposition[y-sz-1:y+sz+1,x-sz:x+sz] == echg
                                elif deposition[y+sz+1,x+sz] == c:
                                    deposition[y-sz+1:y+sz-1,x-sz:x+sz] == echg
                                elif deposition[y,x-sz-1] == c:
                                    deposition[y-sz:y+sz,x-sz-1:x+sz-1] == echg
                                travel[y-sz:y+sz,m2[y]-sz:m2[y]+sz] = echg
                         
                        
                          
                        
                if sp == p:
                    #traveling trhough corona to bowshock
                    if j > c1[i] and j < b1[i]:
                        travel[i-sz:i+sz,j-sz:j+sz] = sp
                    if j > c2[i] and j < b2[i]:
                        travel[i-sz:i+sz,j-sz:j+sz] = sp

                    #deflectiong or passing bowshock: 
                    if j >= b1[i]:
                        d1[i] = d1[i]+(3*lag)
                        if i < Y/2: 
                            if i - d1[i] >= 0:
                                #travel[i-d1,j] = sp
                                travel[i-sz-d1[i]:i+sz-d1[i],j-sz:j+sz] = sp

                    if j >= b2[i]:
                        d2[i] = d2[i]+(3*lag)
                        if i >= Y/2: 
                            if i + d2[i] <= Y-1:
                                travel[i-sz+d2[i]:i+sz+d2[i],j-sz:j+sz] = sp 
            plt.clf()               
            display(travel)
            writer.grab_frame()
            travel = np.copy(deposition)